In [1]:
from tqdm.notebook import tqdm, trange
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
import numpy as np
import random
from matplotlib.animation import FFMpegWriter
from landscapeWithOcean import LandscapeWithOcean

In [2]:
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        ls = LandscapeWithOcean(val,val)
        ax1 = fig.add_subplot(121,projection='3d')
        ax1.plot_surface(NX, NY, elevation[:-1,:-1], cmap=cm.gist_earth, antialiased=False) 
        ax1.set_title('Surface Relief')

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title(f'Elevation, Ocean suface fraction: {round(ls.ComputeOceanVolumeFromOceanLevelParameter(elevation,val,val,oceanLevelParameter),1)}%')

        im = ax2.pcolor(NX,NY,elevation[:-1,:-1],cmap=cm.gist_earth, shading='auto')
        cs = ax2.contour(NX,NY,elevation[:-1,:-1],colors='black')
        
        cbar = fig.colorbar(im,shrink=0.7)
        plt.show()
        plt.pause(0.001)

In [3]:
metadata = dict(title='Final Project - EPS 109', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = init_figure()
iterations = 6
#Setting gridsize and grid values, greater gridsize means less squares that are larger
gridsize = 2 ** (iterations - 1)
NX, NY = np.mgrid[-1:1:1j*gridsize,-1:1:1j*gridsize]
#Setting array that will contain elevation information
elevation  = np.zeros((gridsize + 1, gridsize + 1))

val = np.shape(NX)[0]
#Initializing Ocean parameters
ls = LandscapeWithOcean(val,val)
ls.A = np.zeros((val,val))
oceanLevelParameter=0.3
update_figure()
with writer.saving(fig, "fractal_landscape.mp4", dpi=200):
    for it in tqdm(range(iterations)):
        step = gridsize // 2 ** it
        for y in range(0, gridsize + 1, step):
            #Deciding whether to be positive or negative peak with a value of 1 or 0 
            peak = 1 - (y // step) % 2 if it > 0 else 0
            for x in tqdm(range(step * peak, gridsize + 1, step * (1 + peak))):
                #Dividing the triangles into smaller chunks with increasing iterations
                smoothing = 1 - (x // step) % 2 + 2 * peak if it > 0 else 3
                yval, xval = step * (1 - smoothing // 2), step * (1 - smoothing % 2)
                #Determining boundary elevations of two nearby areas
                bounrdary1 = elevation[y - yval, x - xval]
                bounrdary2 = elevation[y + yval, x + xval]
                #Computing average to use in elevation
                average = (bounrdary1 + bounrdary2) / 2.0
                #Introducing random difference in elevation
                rand_difference = step * (random.random() - 0.5)
                #Computing new elevation based on the boundary elevations with random 
                #rand_difference introduced
                elevation[y,x] = average + rand_difference if it > 0 else 0
                #Updating figure
                update_figure()
                writer.grab_frame()
                fig.clear()

<Figure size 1200x600 with 0 Axes>

/var/folders/75/mx7z1f6115g38jycdyg_0yw00000gn/T/ipykernel_10389/2985175875.py:16: UserWarning: No contour levels were found within the data range.
  cs = ax2.contour(NX,NY,elevation[:-1,:-1],colors='black')


  0%|          | 0/6 [00:00<?, ?it/s]

/var/folders/75/mx7z1f6115g38jycdyg_0yw00000gn/T/ipykernel_10389/2985175875.py:16: UserWarning: No contour levels were found within the data range.
  cs = ax2.contour(NX,NY,elevation[:-1,:-1],colors='black')
